In [5]:
import cudf
import numpy as np
import pandas as pd
import plotly.express as px
import tools

# init paths to data and models
DATA_PATH = '/data/'

SEM_MODEL_NAME = 'sm_ft4_ru_norm'
SEM_MODEL_PATH = DATA_PATH + f'models/{SEM_MODEL_NAME}/'
EVENTS_PATH = DATA_PATH + 'events/lem/events.csv'
TMP_PATH = f'{DATA_PATH}tmp/{SEM_MODEL_NAME}/'

'success'
 
#n_semantic = list(range(40, 130, 10)) + [150, 250, 500, 750, 1000]
n_semantic = list(range(10, 151, 10)) + list(range(200, 1001, 100))
n_clusters = list(range(5, 151))

In [6]:
events = tools.read_events(EVENTS_PATH, remove_hashtag_symbol=False)
print(len(events))
len(events.dropna())


10214


10161

In [10]:
df = tools.read_events(EVENTS_PATH, remove_hashtag_symbol=False)

In [13]:
df.head()

id               title  \
0  40526         #newholland   
1  40527  #щелкунчикплющенко   
2  40528  #щелкунчикплющенко   
3  40529  #щелкунчикплющенко   
4  40530  #щелкунчикплющенко   

                                                tags  \
0  [newholland, новыйгод, newhollandisland, newye...   
1            [щелкунчикплющенко, никита, ледовоешоу]   
2  [щелкунчикплющенко, @rudkovskayaofficial, ледо...   
3  [щелкунчикплющенко, ледовыйдворецспб, icepalac...   
4  [щелкунчикплющенко, плющенко, ледовоешоу, cris...   

                                           postcodes  \
0  ['BsGKwU4gzSC', 'BsGLc1uje9R', 'BsGNytghoG4', ...   
1  ['BsIXbbhgAgC', 'BsIU1R7H_A8', 'BsIY5svHIZA', ...   
2  ['BsIdB8nD3tX', 'BsIdQkMg4fx', 'BsIa4M-gdii', ...   
3  ['BsIpVHrlszJ', 'BsIuA1qH5kC', 'BsIugwgHxmE', ...   
4  ['BsI265XgTKs', 'BsI2YaGB2FA', 'BsI2qaNB-h0', ...   

                                            captions city  \
0  ['#newholland #loft #cristmastree #newyear #wi...  spb   
1  ['#щелкунчикплющенко #зимниеканикулы #волшебст...  spb   
2  ['#никита👑 Юля Алина #щелкунчикплющенко Спасиб...  spb   
3  ['Акробатические этюды или что-то типа того) #...  spb   
4  ['Мы с негативным мишкой с шоу #щелкунчикплюще...  spb   

                                             caption  \
0  ['#newholland #loft #cristmastree #newyear #wi...   
1  ['ледовый шоу щелкунчик с плющенкопочему бы и ...   
2  ['просто восхитительноочень понравиться rudkov...   
3  ['акробатический этюд или чтото тип то #щелкун...   
4  ['ледовый шоу щелкунчик #щелкунчикплющенко #пл...   

                                         description  
0  #newholland #loft #cristmastree #newyear #wint...  
1  ледовый шоу щелкунчик с плющенкопочему бы и не...  
2  просто восхитительноочень понравиться rudkovsk...  
3  акробатический этюд или чтото тип то #щелкунчи...  
4  ледовый шоу щелкунчик #щелкунчикплющенко #плющ...

In [12]:
print(len(df))
len(df.dropna(subset=['description']).id)

10214


10161

In [7]:
!mkdir {TMP_PATH}

for n in n_semantic:
    path = f'{TMP_PATH}{n}/'
    
    df = tools.read_events(EVENTS_PATH, remove_hashtag_symbol=False)
    
    df, X = tools.build_vectors_semantic(df, SEM_MODEL_PATH, n)
    df = tools.calculate_2d(df, X)

    !mkdir {path}
    np.save(path + 'X.npy', X)
    df.to_csv(r'' + path + 'df.csv', index=False)

mkdir: cannot create directory ‘/data/tmp/sm_ft4_ru_norm/’: File exists


AttributeError: 'float' object has no attribute 'split'

In [3]:
df_cross = pd.read_csv('cross_valid_union.csv')

for n in n_semantic:
    path = f'{TMP_PATH}{n}/'
    df = tools.read_events(path + 'df.csv')
    X = np.load(path + 'X.npy')
    
    df = tools.k_means_list(n_clusters, df, X)
    df_scores = tools.calc_scores_list(n_clusters, df, df_cross)
    
    df_scores.to_csv(r'' + path + 'scores_km.csv', index=False)
    df.to_csv(r'' + path + 'df_km.csv', index=False)

In [4]:
df_cross = pd.read_csv('cross_valid_union.csv')

for n in n_semantic:
    path = f'{TMP_PATH}{n}/'
    df = tools.read_events(path + 'df.csv')
    X = np.load(path + 'X.npy')
    
    df = tools.agglomerative_list(n_clusters, df, X)
    df_scores = tools.calc_scores_list(n_clusters, df, df_cross)
    
    df_scores.to_csv(r'' + path + 'scores_ag.csv', index=False)
    df.to_csv(r'' + path + 'df_ag.csv', index=False)

In [4]:
best = tools.find_best_2d_score(n_semantic, TMP_PATH, 'scores_km.csv', 'f1')
print(best)

path = f'{TMP_PATH}{best["n_semantic"]}/'
df = tools.read_events(path + 'df_km.csv')
scores = pd.read_csv(path + 'scores_km.csv')

tools.plot_score(scores, 'f1').show()
tools.plot_events(df, best['n_clusters']).show()
centroids = tools.calc_centroids(df, best['n_clusters'])
fig, _ = tools.plot_centroids(centroids, size_max=80, size_text_tags=1)
fig.show()

tools.plot_scores_3d(n_semantic, n_clusters, TMP_PATH, 'scores_km.csv', 'f1')

{'name': 'f1', 'value': 0.5716272600834492, 'n_clusters': 120, 'n_semantic': 500}


In [5]:
best = tools.find_best_2d_score(n_semantic, TMP_PATH, 'scores_ag.csv', 'f1')
print(best)

path = f'{TMP_PATH}{best["n_semantic"]}/'
df = tools.read_events(path + 'df_ag.csv')
scores = pd.read_csv(path + 'scores_ag.csv')

tools.plot_score(scores, 'f1').show()
tools.plot_events(df, best['n_clusters']).show()
centroids = tools.calc_centroids(df, best['n_clusters'])
fig, _ = tools.plot_centroids(centroids, size_max=80, size_text_tags=1)
fig.show()

tools.plot_scores_3d(n_semantic, n_clusters, TMP_PATH, 'scores_ag.csv', 'f1')

{'name': 'f1', 'value': 0.5656836461126006, 'n_clusters': 36, 'n_semantic': 800}


In [6]:
path = f'{TMP_PATH}{80}/'
df = tools.read_events(path + 'df_km.csv')
scores = pd.read_csv(path + 'scores_km.csv')

tools.plot_score(scores, 'f1').show()
tools.plot_events(df, 60).show()
centroids = tools.calc_centroids(df, 60)
fig, _ = tools.plot_centroids(centroids, size_max=80, size_text_tags=1)
fig.show()

tools.plot_scores_3d(n_semantic, n_clusters, TMP_PATH, 'scores_km.csv', 'f1')